# La batalla de los vecindarios
## Tienda de café en Buenos Aires

### Introducción / Problema comercial

Nuesto cliente es un inversor del área gastronómica, que desea abrir una tienda de café de especialidad en la ciudad de Buenos Aires. La persona en cuestión es un sommelier experto en café, y el público que espera atraer a su negocio es aquel que esté interesado en tomar café de primera calidad en un ambiente relajado. Por lo tanto, desea establecerse en un barrio donde ya haya cafeterías, para captar al público habituado a consumir en ese tipo de locales.
El cliente desea que analicemos cada barrio de la ciudad, buscando la cantidad de cafeterías que tiene cada uno y las características de la mismas (popularidad, precio y opiniones de los usuarios).

### Datos a utilizar

Se utilizarán las siguientes fuentes de datos para confeccionar el informe:
* **Dataset con los barrios de la ciudad de Buenos Aires:** Se utilizará el archivo disponible en https://cdn.buenosaires.gob.ar/datosabiertos/datasets/ministerio-de-educacion/barrios/barrios.geojson. Dado que cada barrio en este archivo es un polígono, se calculará un centroide para cada uno, que será el dato de entrada para las consultas de FourSquare.
* **FourSquare Place Search:** Se buscarán todas las cafeterías presentes en cada barrio
* **FourSquare Get Place Details:** Se buscarán datos de popularidad, precio y rating para cada una de las cafeterías encontradas en el punto anterior.


### Desarrollo de la solución

Empezamos importando todas las librerías que utilizaremos en el proyecto. 

In [2]:
import folium
import json
import shapely
from shapely.geometry import shape, GeometryCollection, Point
import pickle
import requests
import pandas as pd

Para iniciar el análisis, definiremos las coordenadas del centro de la ciudad de Buenos Aires, utilizando para ello las coordenadas del estadio del club Ferrocarril Oeste, conocido por ser el centro geométrico de la ciudad. Mostramos el mapa para asegurarnos que la visualización sea correcta.

In [3]:
ba_center = [-34.6194971, -58.4483353]

In [4]:
map_ba = folium.Map(location=ba_center, zoom_start=12)
map_ba

A continuación importaremos el archivo geoJson con los barrios de la ciudad. Tendremos una variable con la ubicación del archivo en la Web y otra con el archivo que fue descargado en una carpeta local. Mostramos los barrios en el mapa.

In [5]:
barrios_url = 'https://cdn.buenosaires.gob.ar/datosabiertos/datasets/ministerio-de-educacion/barrios/barrios.geojson'
barrios_local = 'barrios.geojson'
map_ba = folium.Map(location=ba_center, zoom_start=12)
folium.GeoJson(barrios_url, name="geojson",style_function=lambda x:{'color': 'blue', 'fill': False}).add_to(map_ba)
map_ba

A continuación generaremos dos listas: en una guardaremos los polígonos correspondientes a cada barrio, y en la otra los nombres de los barrios.

In [6]:
with open(barrios_local) as f:
  features = json.load(f)["features"]

# NOTE: buffer(0) is a trick for fixing scenarios where polygons have overlapping coordinates 
shp_barrios = GeometryCollection([shape(feature["geometry"]).buffer(0) for feature in features])

In [7]:
lista_barrios = list((feature['properties']['BARRIO'] for feature in features))

In [8]:
lista_barrios

['CHACARITA',
 'PATERNAL',
 'VILLA CRESPO',
 'VILLA DEL PARQUE',
 'ALMAGRO',
 'CABALLITO',
 'VILLA SANTA RITA',
 'MONTE CASTRO',
 'VILLA REAL',
 'FLORES',
 'FLORESTA',
 'CONSTITUCION',
 'SAN CRISTOBAL',
 'BOEDO',
 'VELEZ SARSFIELD',
 'VILLA LURO',
 'PARQUE PATRICIOS',
 'MATADEROS',
 'VILLA LUGANO',
 'SAN TELMO',
 'SAAVEDRA',
 'COGHLAN',
 'VILLA URQUIZA',
 'COLEGIALES',
 'BALVANERA',
 'VILLA GRAL. MITRE',
 'PARQUE CHAS',
 'AGRONOMIA',
 'VILLA ORTUZAR',
 'BARRACAS',
 'PARQUE AVELLANEDA',
 'PARQUE CHACABUCO',
 'NUEVA POMPEYA',
 'PALERMO',
 'VILLA RIACHUELO',
 'VILLA SOLDATI',
 'VILLA PUEYRREDON',
 'VILLA DEVOTO',
 'LINIERS',
 'VERSALLES',
 'PUERTO MADERO',
 'MONSERRAT',
 'SAN NICOLAS',
 'BELGRANO',
 'RECOLETA',
 'RETIRO',
 'NUÃ‘EZ',
 'BOCA']

Calculamos el centroide de cada barrio, y los graficamos en el mapa. Graficamos también un circulo de 2000m alrededor de cada centroide.

In [9]:
centroide_barrios = []
for barrio in shp_barrios:
    centroide = barrio.centroid.coords[0]
    centroide_barrios.append(centroide)
centroide_barrios

[(-58.454180123557734, -34.5883686597017),
 (-58.46866483674234, -34.597421176897754),
 (-58.442724948235764, -34.59882966797722),
 (-58.490677076738244, -34.604246638188634),
 (-58.4217445234198, -34.6092272592652),
 (-58.44360306345077, -34.61682541891128),
 (-58.48295678746961, -34.61619345688689),
 (-58.50658094855397, -34.619297761788005),
 (-58.526038690746745, -34.619493189642185),
 (-58.45826804456002, -34.63680311748685),
 (-58.48358753009863, -34.627685776381824),
 (-58.3843881201894, -34.62504411439053),
 (-58.40188403398473, -34.62386450416032),
 (-58.41883953610525, -34.629959921206925),
 (-58.49327669041595, -34.63136139129974),
 (-58.50272905510572, -34.636413257818795),
 (-58.401674941202245, -34.637550453754656),
 (-58.501737029500894, -34.65837345114918),
 (-58.476167029092416, -34.67499310701554),
 (-58.371541034906436, -34.621520466643766),
 (-58.48874459528289, -34.55307605765025),
 (-58.474944327825554, -34.5606237746284),
 (-58.48785550169213, -34.571540521723),


In [10]:
map_ba = folium.Map(location=ba_center, zoom_start=12)
folium.GeoJson(barrios_url, name="geojson",style_function=lambda x:{'color': 'blue', 'fill': False}).add_to(map_ba)
for barrio in centroide_barrios:
    folium.Marker([barrio[1],barrio[0]]).add_to(map_ba)
    folium.Circle([barrio[1],barrio[0]], radius=2000, color='red', fill=False).add_to(map_ba)
map_ba

Se observa que, si hacemos una busqueda de 2000m alrededor de cada centroide, cubrimos toda la ciudad. Los resultados repetidos los podemos filtrar a posteriori.

Definimos las variables necesarias para las consultas a FourSquare, usando la API v3.

In [11]:
token_foursquare = 'fsq3avfJIlLBM1et/BnaqBHZa3Dn56pyhs33CGm13GJU9BQ='

In [12]:
headers = {
    "Accept": "application/json",
    "Authorization": token_foursquare
}
LIMIT = 50 #La nueva API solo acepta LIMIT menor o igual que 50

Definimos una función que busca lugares cercanos a una ubicación geográfica, definida por unas coordenadas. La función filtrará los lugares por categoría y buscará en un radio determinado. La categoría default será 13032 (Dining and Drinking > Cafes, Coffee, and Tea Houses) y el radio default 2000m. Para mas detalles sobre las categorías, ver https://location.foursquare.com/places/docs/categories

In [13]:
def getNearbyVenues(coordinates, categories = '13032', radius=2000):
    
    venues_list=[]
    for lng,lat in coordinates:
        print('.',end='')
            
        # crear la URL de solicitud de API v3, los parametros se pasan en un diccionario y el token en el header
        url = "https://api.foursquare.com/v3/places/search"
        coord = '{},{}'.format(lat,lng)
        params = {"ll": coord,
          "limit": LIMIT,
          "radius": radius,
          "categories": categories}
            
        # solicitud GET
        results = requests.request("GET", url, params=params, headers=headers).json()
        venues = results['results']

        
        # regresa solo información relevante de cada sitio cercano, cuando hay un sitio sin categoría da error y lo ignoramos
        try:
            for v in venues:
                venues_list.append([(
                    v['fsq_id'],
                    v['name'],
                    v['geocodes']['main']['latitude'],
                    v['geocodes']['main']['longitude'],
                    v['categories'][0]['name'])])
        except:
            pass
    
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['fsq_id', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

La consulta solo se hace una vez, y se guardan los resultados localmente en un Pickle. Solo se ejecuta la consulta a FourSquare si el Pickle no se encuentra en el disco.

In [14]:
try:
    with open('cafes.pkl', 'rb') as f:
        df_cafes = pickle.load(f)
    print('Cafes leídos desde el disco')
    
except:
    df_cafes = getNearbyVenues(centroide_barrios)
    df_cafes.drop_duplicates(inplace=True)
    with open('cafes.pkl', 'wb') as f:
        pickle.dump(df_cafes, f)


................................................

Ahora el DataFrame **df_cafes** contiene los datos de todos los cafes encontrados, sin duplicados. Revisamos los resultados y hacemos un análisis de alto nivel del DataFrame.

In [51]:
df_cafes

fsq_id                        Venue  Venue Latitude  \
0     59d692e3a0215b2c4a455503                La Noire Café      -34.587667   
1     513f64c9e4b0844643bc8cfb        Heladeria Scannapieco      -34.583148   
2     5505bc17498e07e2400d6f1f                     Rapa Nui      -34.572161   
3     4b9a52e2f964a52064ac35e3              Eterna Cadencia      -34.584441   
4     5734f25b498ef99659a726ed                    Vive Café      -34.581823   
...                        ...                          ...             ...   
2147  4d7d0bf36152b60c39eb9c26                   Maria Rojo      -34.619743   
2148  56a62a38498ed5378bccda15              Blue café y Bar      -34.616258   
2151  61d863a524d9b151bc5cf8b7                       Merope      -34.620230   
2152  4edecd578b81340ef054d4f9            Le Volant Voiture      -34.620802   
2153  5016facce4b0d8233f9722de  Centro de Estudios del Café      -34.620990   

      Venue Longitude                 Venue Category  
0          -58.442770                           Café  
1          -58.444771                           Café  
2          -58.459074  Cafes, Coffee, and Tea Houses  
3          -58.436098  Cafes, Coffee, and Tea Houses  
4          -58.435947                           Café  
...               ...                            ...  
2147       -58.369070                           Café  
2148       -58.362067                    Coffee Shop  
2151       -58.371750                           Café  
2152       -58.372466  Cafes, Coffee, and Tea Houses  
2153       -58.373906                           Café  

[964 rows x 5 columns]

In [52]:
df_cafes.reset_index(inplace=True)

In [53]:
df_cafes.describe(include='all')

index                    fsq_id      Venue  Venue Latitude  \
count    964.000000                       964        964      964.000000   
unique          NaN                       964        747             NaN   
top             NaN  59d692e3a0215b2c4a455503  Starbucks             NaN   
freq            NaN                         1         61             NaN   
mean     838.783195                       NaN        NaN      -34.604459   
std      617.886675                       NaN        NaN        0.028604   
min        0.000000                       NaN        NaN      -34.687718   
25%      303.500000                       NaN        NaN      -34.625653   
50%      743.000000                       NaN        NaN      -34.607174   
75%     1168.250000                       NaN        NaN      -34.584994   
max     2153.000000                       NaN        NaN      -34.533324   

        Venue Longitude Venue Category  
count        964.000000            964  
unique              NaN             21  
top                 NaN           Café  
freq                NaN            418  
mean         -58.442541            NaN  
std            0.046258            NaN  
min          -58.541501            NaN  
25%          -58.477415            NaN  
50%          -58.447376            NaN  
75%          -58.402804            NaN  
max          -58.355098            NaN

In [54]:
df_cafes['Venue Category'].value_counts()

Café                             418
Coffee Shop                      366
Bar                               85
Cafes, Coffee, and Tea Houses     30
Bakery                            28
Tea Room                          18
Burger Joint                       2
Bistro                             2
Sports Bar                         2
Music Venue                        2
Bubble Tea Shop                    1
Concert Hall                       1
Buffet                             1
Dance Hall                         1
Night Club                         1
Arts and Entertainment             1
Rock Club                          1
Bagel Shop                         1
Wine Bar                           1
Pet Café                           1
Beer Garden                        1
Name: Venue Category, dtype: int64

Finalmente, mostramos todos los cafes encontrados sobre el mapa. Se observa que algunos resultados quedan fuera de la ciudad, los mismos serán filtrados cuando le asignemos un barrio a cada cafe.

In [55]:
map_ba = folium.Map(location=ba_center, zoom_start=12)
folium.GeoJson(barrios_url, name="geojson",style_function=lambda x:{'color': 'blue', 'fill': False}).add_to(map_ba)
for index, row in df_cafes.iterrows():
    folium.CircleMarker([row['Venue Latitude'],row['Venue Longitude']]
                        ,radius=3,
                        color='red',
                        fill=True,
                        fill_color='red',
                        fill_opacity=1).add_to(map_ba)
map_ba

Nuestro cliente está interesado en el perfil de las cafeterias presentes en cada barrio, por lo que utilizaremos otro endpoint de la API de FourSquare para traer tres detalles de cada cafe: Popularity (la cantidad de visitas que recibe, en una escala de 0 a 1), Price (el nivel de precios del cafe, en una escala de 1 a 4) y Rating (el puntaje promedio que le dan los visitantes, en una escala de 0 a 10). Para mas detalles sobre el endpoint, ver https://location.foursquare.com/developer/reference/place-details.

In [29]:
def getVenuesDetails(fsq):
    url = "https://api.foursquare.com/v3/places/{}".format(fsq)
    params = {"fields": 'rating,popularity,price'}
    # solicitud GET
    results = requests.request("GET", url, params=params, headers=headers).json()
    return(results)

In [30]:
def getAllVenuesDetails(df):
    fsq_list = []
    popularity_list = []
    price_list = []
    rating_list = []
    for index, row in df.iterrows():
        print(index,end=',')
        fsq_list.append(row['fsq_id'])
        try:
            details = getVenuesDetails(row['fsq_id'])
            popularity_list.append(details.get('popularity'))
            price_list.append(details.get('price'))
            rating_list.append(details.get('rating'))
        except:
            pass
        
    df_out = pd.DataFrame(list(zip(fsq_list, popularity_list, price_list, rating_list)),
                          columns =['fsq_id', 'popularity','price','rating'])
    return(df_out)

Al igual que en la consulta anterior, la consulta solo se hace una vez, y se guardan los resultados localmente en un Pickle. Solo se ejecuta la consulta a FourSquare si el Pickle no se encuentra en el disco.

In [33]:
try:
    with open('cafes_detalles.pkl', 'rb') as f:
        df_cafes_detalles = pickle.load(f)
    print('Detalles de los cafes leídos desde el disco')
    
except:
    df_cafes_detalles = getAllVenuesDetails(df_cafes)
    with open('cafes_detalles.pkl', 'wb') as f:
        pickle.dump(df_cafes_detalles, f)


0,1,2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63,64,65,66,67,68,69,70,71,72,73,74,75,76,77,78,79,80,81,82,83,84,85,86,87,88,89,90,91,92,93,94,95,96,97,98,99,100,101,102,103,104,105,106,107,108,109,110,111,112,113,114,115,116,117,118,119,120,121,122,123,124,125,126,127,128,129,130,131,132,133,134,135,136,137,138,139,140,141,142,143,144,145,146,147,148,149,150,151,152,153,154,155,156,157,158,159,160,161,162,163,164,165,166,167,168,169,170,171,172,173,174,175,176,177,178,179,180,181,182,183,184,185,186,187,188,189,190,191,192,193,194,195,196,197,198,199,200,201,202,203,204,205,206,207,208,209,210,211,212,213,214,215,216,217,218,219,220,221,222,223,224,225,226,227,228,229,230,231,232,233,234,235,236,237,238,239,240,241,242,243,244,245,246,247,248,249,250,251,252,253,254,255,256,257,258,259,260,261,262,263,264,265,266,267,268,269,270,271,272,273,274,275,276,27

Ahora el DataFrame **df_cafes_detalles** contiene los detalles de todos los cafes encontrados. Revisamos los resultados y hacemos un análisis de alto nivel del DataFrame.

In [57]:
df_cafes_detalles

fsq_id  popularity  price  rating
0    59d692e3a0215b2c4a455503    0.985346    1.0     8.3
1    513f64c9e4b0844643bc8cfb    0.987874    3.0     8.3
2    5505bc17498e07e2400d6f1f    0.997993    3.0     9.4
3    4b9a52e2f964a52064ac35e3    0.965526    NaN     9.0
4    5734f25b498ef99659a726ed    0.993516    1.0     8.8
..                        ...         ...    ...     ...
959  4d7d0bf36152b60c39eb9c26    0.114087    1.0     NaN
960  56a62a38498ed5378bccda15    0.153476    1.0     NaN
961  61d863a524d9b151bc5cf8b7    0.609504    1.0     NaN
962  4edecd578b81340ef054d4f9    0.588430    2.0     NaN
963  5016facce4b0d8233f9722de    0.518144    1.0     NaN

[964 rows x 4 columns]

In [58]:
df_cafes_detalles.describe(include='all')

fsq_id  popularity       price      rating
count                        964  819.000000  808.000000  460.000000
unique                       964         NaN         NaN         NaN
top     59d692e3a0215b2c4a455503         NaN         NaN         NaN
freq                           1         NaN         NaN         NaN
mean                         NaN    0.825978    1.157178    7.129783
std                          NaN    0.272219    0.432620    0.953679
min                          NaN    0.000199    1.000000    4.600000
25%                          NaN    0.828711    1.000000    6.375000
50%                          NaN    0.963024    1.000000    7.200000
75%                          NaN    0.985796    1.000000    7.825000
max                          NaN    0.999389    4.000000    9.400000

Creamos un nuevo DataFrame, uniendo los datos básicos de cada cafe con los detalles. Lo llamamos **df_cafes_completo**

In [59]:
df_cafes_completo = df_cafes.merge(df_cafes_detalles,on='fsq_id')

In [60]:
df_cafes_completo

index                    fsq_id                        Venue  \
0        0  59d692e3a0215b2c4a455503                La Noire Café   
1        1  513f64c9e4b0844643bc8cfb        Heladeria Scannapieco   
2        2  5505bc17498e07e2400d6f1f                     Rapa Nui   
3        3  4b9a52e2f964a52064ac35e3              Eterna Cadencia   
4        4  5734f25b498ef99659a726ed                    Vive Café   
..     ...                       ...                          ...   
959   2147  4d7d0bf36152b60c39eb9c26                   Maria Rojo   
960   2148  56a62a38498ed5378bccda15              Blue café y Bar   
961   2151  61d863a524d9b151bc5cf8b7                       Merope   
962   2152  4edecd578b81340ef054d4f9            Le Volant Voiture   
963   2153  5016facce4b0d8233f9722de  Centro de Estudios del Café   

     Venue Latitude  Venue Longitude                 Venue Category  \
0        -34.587667       -58.442770                           Café   
1        -34.583148       -58.444771                           Café   
2        -34.572161       -58.459074  Cafes, Coffee, and Tea Houses   
3        -34.584441       -58.436098  Cafes, Coffee, and Tea Houses   
4        -34.581823       -58.435947                           Café   
..              ...              ...                            ...   
959      -34.619743       -58.369070                           Café   
960      -34.616258       -58.362067                    Coffee Shop   
961      -34.620230       -58.371750                           Café   
962      -34.620802       -58.372466  Cafes, Coffee, and Tea Houses   
963      -34.620990       -58.373906                           Café   

     popularity  price  rating  
0      0.985346    1.0     8.3  
1      0.987874    3.0     8.3  
2      0.997993    3.0     9.4  
3      0.965526    NaN     9.0  
4      0.993516    1.0     8.8  
..          ...    ...     ...  
959    0.114087    1.0     NaN  
960    0.153476    1.0     NaN  
961    0.609504    1.0     NaN  
962    0.588430    2.0     NaN  
963    0.518144    1.0     NaN  

[964 rows x 9 columns]

Ahora le asignaremos un barrio a cada cafe encontrado. Para eso usamos la función **contains** de Shapely, que devuelve True si un punto está contenido dentro de un polígono. Para cada cafe, iteramos la función en todos los polígonos de los barrios. Si la función devuelve False para todos los barrios, retornamos None.

In [61]:
barrios_list = []
for index,row in df_cafes.iterrows():
    barrio_asignar = None
    for barrio,nombre_barrio in zip(shp_barrios,lista_barrios):
        if barrio.contains(Point(row['Venue Longitude'],row['Venue Latitude'])):
            barrio_asignar = nombre_barrio
    barrios_list.append(barrio_asignar)

In [62]:
len(barrios_list)

964

In [63]:
df_cafes_completo['Barrio'] = barrios_list

In [64]:
df_cafes_completo

index                    fsq_id                        Venue  \
0        0  59d692e3a0215b2c4a455503                La Noire Café   
1        1  513f64c9e4b0844643bc8cfb        Heladeria Scannapieco   
2        2  5505bc17498e07e2400d6f1f                     Rapa Nui   
3        3  4b9a52e2f964a52064ac35e3              Eterna Cadencia   
4        4  5734f25b498ef99659a726ed                    Vive Café   
..     ...                       ...                          ...   
959   2147  4d7d0bf36152b60c39eb9c26                   Maria Rojo   
960   2148  56a62a38498ed5378bccda15              Blue café y Bar   
961   2151  61d863a524d9b151bc5cf8b7                       Merope   
962   2152  4edecd578b81340ef054d4f9            Le Volant Voiture   
963   2153  5016facce4b0d8233f9722de  Centro de Estudios del Café   

     Venue Latitude  Venue Longitude                 Venue Category  \
0        -34.587667       -58.442770                           Café   
1        -34.583148       -58.444771                           Café   
2        -34.572161       -58.459074  Cafes, Coffee, and Tea Houses   
3        -34.584441       -58.436098  Cafes, Coffee, and Tea Houses   
4        -34.581823       -58.435947                           Café   
..              ...              ...                            ...   
959      -34.619743       -58.369070                           Café   
960      -34.616258       -58.362067                    Coffee Shop   
961      -34.620230       -58.371750                           Café   
962      -34.620802       -58.372466  Cafes, Coffee, and Tea Houses   
963      -34.620990       -58.373906                           Café   

     popularity  price  rating         Barrio  
0      0.985346    1.0     8.3      CHACARITA  
1      0.987874    3.0     8.3      CHACARITA  
2      0.997993    3.0     9.4     COLEGIALES  
3      0.965526    NaN     9.0        PALERMO  
4      0.993516    1.0     8.8        PALERMO  
..          ...    ...     ...            ...  
959    0.114087    1.0     NaN      SAN TELMO  
960    0.153476    1.0     NaN  PUERTO MADERO  
961    0.609504    1.0     NaN      SAN TELMO  
962    0.588430    2.0     NaN      SAN TELMO  
963    0.518144    1.0     NaN      SAN TELMO  

[964 rows x 10 columns]

Revisamos los cafes que quedaron con el barrio en None

In [65]:
df_cafes_sin_barrio = df_cafes_completo[df_cafes_completo['Barrio'].isnull()].reset_index()

In [66]:
map_ba = folium.Map(location=ba_center, zoom_start=12)
folium.GeoJson(barrios_url, name="geojson",style_function=lambda x:{'color': 'blue', 'fill': False}).add_to(map_ba)
for index, row in df_cafes_sin_barrio.iterrows():
    folium.CircleMarker([row['Venue Latitude'],row['Venue Longitude']]
                        ,radius=3,
                        color='red',
                        fill=True,
                        fill_color='red',
                        fill_opacity=1).add_to(map_ba)
map_ba

Se compureba que todos los cafes sin barrio están fuera de la zona de análisis, por lo que los descartamos.

In [67]:
df_cafes_completo = df_cafes_completo[df_cafes_completo['Barrio'].isnull() == False]

In [68]:
df_cafes_completo

index                    fsq_id                        Venue  \
0        0  59d692e3a0215b2c4a455503                La Noire Café   
1        1  513f64c9e4b0844643bc8cfb        Heladeria Scannapieco   
2        2  5505bc17498e07e2400d6f1f                     Rapa Nui   
3        3  4b9a52e2f964a52064ac35e3              Eterna Cadencia   
4        4  5734f25b498ef99659a726ed                    Vive Café   
..     ...                       ...                          ...   
959   2147  4d7d0bf36152b60c39eb9c26                   Maria Rojo   
960   2148  56a62a38498ed5378bccda15              Blue café y Bar   
961   2151  61d863a524d9b151bc5cf8b7                       Merope   
962   2152  4edecd578b81340ef054d4f9            Le Volant Voiture   
963   2153  5016facce4b0d8233f9722de  Centro de Estudios del Café   

     Venue Latitude  Venue Longitude                 Venue Category  \
0        -34.587667       -58.442770                           Café   
1        -34.583148       -58.444771                           Café   
2        -34.572161       -58.459074  Cafes, Coffee, and Tea Houses   
3        -34.584441       -58.436098  Cafes, Coffee, and Tea Houses   
4        -34.581823       -58.435947                           Café   
..              ...              ...                            ...   
959      -34.619743       -58.369070                           Café   
960      -34.616258       -58.362067                    Coffee Shop   
961      -34.620230       -58.371750                           Café   
962      -34.620802       -58.372466  Cafes, Coffee, and Tea Houses   
963      -34.620990       -58.373906                           Café   

     popularity  price  rating         Barrio  
0      0.985346    1.0     8.3      CHACARITA  
1      0.987874    3.0     8.3      CHACARITA  
2      0.997993    3.0     9.4     COLEGIALES  
3      0.965526    NaN     9.0        PALERMO  
4      0.993516    1.0     8.8        PALERMO  
..          ...    ...     ...            ...  
959    0.114087    1.0     NaN      SAN TELMO  
960    0.153476    1.0     NaN  PUERTO MADERO  
961    0.609504    1.0     NaN      SAN TELMO  
962    0.588430    2.0     NaN      SAN TELMO  
963    0.518144    1.0     NaN      SAN TELMO  

[949 rows x 10 columns]

Ahora tenemos 949 cafes, cada uno con su barrio asignado y el detalle de Popularity, Price y Rating. Hacemos una estadística agrupada por barrio para evaluarlos.

In [69]:
df_cafes_porbarrio = df_cafes_completo.groupby('Barrio').agg({'fsq_id':'count',
                                         'popularity':'mean',
                                         'price':'mean',
                                         'rating': 'mean'})

In [70]:
df_cafes_porbarrio.rename(columns = {'fsq_id':'cantidad'},inplace=True)

In [71]:
df_cafes_porbarrio

cantidad  popularity     price    rating
Barrio                                                     
AGRONOMIA                 7    0.669556  1.166667  7.566667
ALMAGRO                  19    0.932654  1.176471  7.025000
BALVANERA                23    0.933054  1.150000  6.861538
BARRACAS                 28    0.726150  1.000000  6.500000
BELGRANO                 54    0.909535  1.188679  7.108333
BOCA                     17    0.660138  1.125000  6.114286
BOEDO                    12    0.851420  1.111111  7.342857
CABALLITO                66    0.796414  1.078125  6.794286
CHACARITA                11    0.857768  1.200000  7.366667
COGHLAN                   5    0.969408  1.000000  6.833333
COLEGIALES               19    0.911910  1.157895  7.309091
CONSTITUCION             14    0.652011  1.142857  5.800000
FLORES                   46    0.700867  1.027778  6.846154
FLORESTA                 13    0.863135  1.000000  6.300000
LINIERS                  24    0.812120  1.071429  7.233333
MATADEROS                20    0.709006  1.181818  6.440000
MONSERRAT                41    0.875101  1.230769  6.980769
MONTE CASTRO             12    0.624525  1.125000  6.400000
NUEVA POMPEYA             9    0.117773  1.000000       NaN
NUÃ‘EZ                   21    0.869576  1.142857  6.600000
PALERMO                  71    0.964805  1.260870  7.506250
PARQUE AVELLANEDA         5    0.948009  1.000000       NaN
PARQUE CHACABUCO         10    0.911468  1.125000  7.500000
PARQUE CHAS               8    0.917006  1.166667  6.333333
PARQUE PATRICIOS         22    0.623767  1.153846  6.700000
PATERNAL                 10    0.661401  1.000000  7.400000
PUERTO MADERO            13    0.770690  1.000000  7.428571
RECOLETA                 33    0.979433  1.212121  7.455172
RETIRO                   19    0.987039  1.000000  7.738889
SAAVEDRA                 30    0.721366  1.178571  6.725000
SAN CRISTOBAL            10    0.549112  1.000000  5.900000
SAN NICOLAS              42    0.962342  1.285714  7.539474
SAN TELMO                19    0.812374  1.157895  7.554545
VELEZ SARSFIELD           4    0.947881  1.000000  6.800000
VERSALLES                 2    0.753961  2.000000       NaN
VILLA CRESPO             28    0.911757  1.130435  7.254545
VILLA DEL PARQUE         25    0.694623  1.150000  6.642857
VILLA DEVOTO             37    0.762516  1.093750  6.729412
VILLA GRAL. MITRE         9    0.845869  1.375000  6.225000
VILLA LUGANO              8    0.576006  1.000000  7.400000
VILLA LURO               11    0.796648  1.222222  7.500000
VILLA ORTUZAR            11    0.810702  1.285714  6.875000
VILLA PUEYRREDON         10    0.650016  1.000000  8.200000
VILLA REAL                4         NaN       NaN       NaN
VILLA RIACHUELO           1    0.981049  1.000000       NaN
VILLA SANTA RITA         11    0.635463  1.333333  7.200000
VILLA SOLDATI             1         NaN       NaN       NaN
VILLA URQUIZA            34    0.693935  1.235294  6.988235

Definimos dos umbrales: Popularity mayor a 0.95 y Rating mayor a 7, para buscar los barrios que mejor se ajusten a los pedidos del cliente.

In [72]:
popularity_umbral = 0.95
rating_umbral = 7
df_cafes_porbarrio[(df_cafes_porbarrio['popularity']>popularity_umbral) & (df_cafes_porbarrio['rating']>rating_umbral)].sort_values('cantidad',ascending=False)

cantidad  popularity     price    rating
Barrio                                               
PALERMO            71    0.964805  1.260870  7.506250
SAN NICOLAS        42    0.962342  1.285714  7.539474
RECOLETA           33    0.979433  1.212121  7.455172
RETIRO             19    0.987039  1.000000  7.738889

El resultado de cuatro barrios objetivo parece un resultado aceptable para una primer entrega al cliente. Por lo tanto, guardaremos esta lista y armaremos un nuevo dataframe **df_cafes_barrios_top**, con los cafes incluidos en los barrios objetivo.

In [73]:
barrios_top = list(df_cafes_porbarrio[(df_cafes_porbarrio['popularity']>0.95) & (df_cafes_porbarrio['rating']>7)].sort_values('cantidad',ascending=False).index)

In [74]:
barrios_top

['PALERMO', 'SAN NICOLAS', 'RECOLETA', 'RETIRO']

In [75]:
df_cafes_barrios_top = df_cafes_completo[df_cafes_completo['Barrio'].isin(barrios_top)]

In [76]:
df_cafes_barrios_top

index                    fsq_id                               Venue  \
3        3  4b9a52e2f964a52064ac35e3                     Eterna Cadencia   
4        4  5734f25b498ef99659a726ed                           Vive Café   
5        5  53652033498e2b4b27e35915                         Adorado Bar   
6        6  542c714a498ed1d8ff638938  Lab. Training Center & Coffee Shop   
7        7  5d0e94f444627d0023e21d0a                         Cuervo Café   
..     ...                       ...                                 ...   
909   2004  5920e339ee628b240bcb25a3                           Starbucks   
910   2046  4f8c6d03e4b060b7fa3b0796                               Dandy   
911   2047  4cb605cf56fca1cdab445318                        Cafe Valerio   
912   2050  4dcac8ba887769ff3d572d8b             Arenales Restó & Coffee   
913   2054  4b5dc0d5f964a520f06929e3                        Saint Moritz   

     Venue Latitude  Venue Longitude                 Venue Category  \
3        -34.584441       -58.436098  Cafes, Coffee, and Tea Houses   
4        -34.581823       -58.435947                           Café   
5        -34.579740       -58.436125                           Café   
6        -34.586045       -58.436904                           Café   
7        -34.581079       -58.436499                    Coffee Shop   
..              ...              ...                            ...   
909      -34.591471       -58.375018                    Coffee Shop   
910      -34.595026       -58.378726                            Bar   
911      -34.602454       -58.377962                            Bar   
912      -34.594333       -58.384640                           Café   
913      -34.597780       -58.378646                            Bar   

     popularity  price  rating       Barrio  
3      0.965526    NaN     9.0      PALERMO  
4      0.993516    1.0     8.8      PALERMO  
5      0.979859    1.0     8.8      PALERMO  
6      0.990093    2.0     8.5      PALERMO  
7      0.992628    1.0     8.6      PALERMO  
..          ...    ...     ...          ...  
909    0.987263    1.0     7.1       RETIRO  
910    0.992281    1.0     6.6       RETIRO  
911    0.993908    1.0     6.9  SAN NICOLAS  
912    0.983461    1.0     6.6       RETIRO  
913    0.992030    1.0     6.4       RETIRO  

[165 rows x 10 columns]

In [77]:
df_cafes_barrios_top.reset_index(inplace=True)

Finalmente, confeccionamos el mapa que se presentará al cliente para continuar con el análisis. En dicho mapa están resaltados los cuatro barrios preseleccionados, con todos los cafes de cada uno de ellos. Al deslizar el mouse encima de un cafe se pueden ver los detalles del mismo (nombre, popularidad redondeada a dos decimales, precio y rating).

In [82]:
map_ba = folium.Map(location=ba_center, zoom_start=12)
for barrio,nombre_barrio in zip(shp_barrios,lista_barrios):
    if nombre_barrio in barrios_top:
        folium.GeoJson(barrio,style_function=lambda x:{'color': 'blue', 'fill': True}).add_to(map_ba)
for barrio,nombre_barrio in zip(shp_barrios,lista_barrios):
    if nombre_barrio not in barrios_top:
        folium.GeoJson(barrio,style_function=lambda x:{'color': 'blue', 'fill': False}).add_to(map_ba)
for index, row in df_cafes_barrios_top.iterrows():
    etiqueta = 'Nombre = {}, Popularidad = {}, Precio = {}, Rating = {}'.format(row['Venue'],
                                                                                '%.2f' % row['popularity'],
                                                                                row['price'],
                                                                                row['rating'])
    folium.CircleMarker([row['Venue Latitude'],row['Venue Longitude']]
                        ,radius=3,
                        color='red',
                        fill=True,
                        fill_color='red',
                        fill_opacity=1,
                        tooltip = etiqueta).add_to(map_ba)

map_ba

Con esto concluye el análisis del caso. Los siguientes pasos consisten en reunirse con el cliente, mostrarle este primer trabajo y obtener feedback sobre cualquier necesidad extra que pudiera resolverse mediante el análisis de los datos.